# Qui va sobreviure al Titanic?

En aquest exercici, utilitzarem les dades del Titanic per predir si un passatger va sobreviure o no al naufragi. 
Veurem diferent formes de fer-ho; amb diversos graus d'automatisme.

## Human learn

Human learn és una llibreria que ens permet combinar el machine learning amb el coneixement humà de forma senzilla.

In [1]:
# Carreguem les llibreries i les dades

In [2]:
# Instal·lem la llibreria
!pip install git+https://github.com/koaning/human-learn.git

  Cloning https://github.com/koaning/human-learn.git to /private/var/folders/zm/06zm__c5637bs4z8mhp4pfph0000gn/T/pip-req-build-u6_658u_
  Running command git clone --filter=blob:none --quiet https://github.com/koaning/human-learn.git /private/var/folders/zm/06zm__c5637bs4z8mhp4pfph0000gn/T/pip-req-build-u6_658u_
  Resolved https://github.com/koaning/human-learn.git to commit e83ea4d88ade6686b6eac1f02790beff4a324d84
  Preparing metadata (setup.py) ... done

[notice] A new release of pip available: 22.3.1 -> 23.3.2
[notice] To update, run: pip install --upgrade pip


In [3]:
from hulearn.datasets import load_titanic

In [4]:
df = load_titanic(as_frame=True)
df

survived  pclass                                               name  \
0           0       3                            Braund, Mr. Owen Harris   
1           1       1  Cumings, Mrs. John Bradley (Florence Briggs Th...   
2           1       3                             Heikkinen, Miss. Laina   
3           1       1       Futrelle, Mrs. Jacques Heath (Lily May Peel)   
4           0       3                           Allen, Mr. William Henry   
..        ...     ...                                                ...   
709         0       3               Rice, Mrs. William (Margaret Norton)   
710         0       2                              Montvila, Rev. Juozas   
711         1       1                       Graham, Miss. Margaret Edith   
712         1       1                              Behr, Mr. Karl Howell   
713         0       3                                Dooley, Mr. Patrick   

        sex   age     fare  sibsp  parch  
0      male  22.0   7.2500      1      0  
1    female  38.0  71.2833      1      0  
2    female  26.0   7.9250      0      0  
3    female  35.0  53.1000      1      0  
4      male  35.0   8.0500      0      0  
..      ...   ...      ...    ...    ...  
709  female  39.0  29.1250      0      5  
710    male  27.0  13.0000      0      0  
711  female  19.0  30.0000      0      0  
712    male  26.0  30.0000      0      0  
713    male  32.0   7.7500      0      0  

[714 rows x 8 columns]

In [5]:
from sklearn.model_selection import train_test_split

# Preparem les dades: separem les variables explicatives de la variable objectiu i creem els conjunts d'entrenament i de test
X_train, X_test, y_train, y_test = train_test_split(
    df.drop(['name', 'survived'], axis=1), df['survived'], test_size=0.25, random_state=42)

### Classificació amb una funció

En aquest primer exemple, utilitzarem una funció per classificar els passatgers. Es tracta d'una funció molt senzilla que classifica els passatgers en funció del preu del bitllet. El plantejament és que els passatgers que van pagar més tenien més probabilitats de sobreviure.

In [6]:
# FunctionClassifier ens permet crear un classificador a partir d'una funció
from hulearn.classification import FunctionClassifier

In [7]:
# Utilitzarem el FunctionClassifier per crear un classificador que utilitzi el preu del bitllet per predir si un passatger va sobreviure o no

def classificador_preu_bitllet(df, preu_minim=20):
    """
    Classifica els passatgers en funció del preu del bitllet
    El plantejament és que els passatgers que van pagar més tenien més probabilitats de sobreviure.
    El valor per defecte és 20, però podem canviar-lo
    """
    return (df['fare'] > preu_minim).astype(int)


model = FunctionClassifier(classificador_preu_bitllet)

# Preparem el classificador
model.fit(X_train, y_train)

FunctionClassifier(func=<function classificador_preu_bitllet at 0x120dda340>)

### Evaluem el classificador

In [8]:
from sklearn.metrics import classification_report

print(classification_report(y_test, model.predict(X_test)))

              precision    recall  f1-score   support

           0       0.73      0.69      0.71       107
           1       0.57      0.61      0.59        72

    accuracy                           0.66       179
   macro avg       0.65      0.65      0.65       179
weighted avg       0.66      0.66      0.66       179


El rendiment del classificador és prou dolent. Segurament, el preu del bitllet no és una bona variable per predir si un passatger va sobreviure o no. Així i tot intentarem millorar el seu rendiment afinant el paràmetre preu_minim.

Utilitzarem GridSearchCV per trobar el millor valor per preu_minim. GridSearchCV ens permet fer una cerca en graella per trobar els millors paràmetres, la puntuació vindrà donada per la precisió (accuracy), la precisió (precision) i la sensibilitat (recall).

**Accuracy**: Quantes prediccions són correctes?
**Precision**: Quantes prediccions positives són correctes?
**Recall**: Quantes prediccions positives són correctes de totes les positives?

In [9]:
import numpy as np
from sklearn.metrics import make_scorer, accuracy_score, precision_score, recall_score
from sklearn.model_selection import GridSearchCV

# Creem un classificador amb un preu mínim de 20
mod = FunctionClassifier(classificador_preu_bitllet, preu_minim=20)

# L'objecte GridSearchCV ens permet fer una cerca en graella per trobar els millors paràmetres.
# En aquest cas, buscarem el millor preu mínim per classificar els passatgers
grid = GridSearchCV(mod,
                    cv=2,
                    param_grid={'preu_minim': np.linspace(0, 100, 30)},
                    scoring={'accuracy': make_scorer(accuracy_score),
                             'precision': make_scorer(precision_score),
                             'recall': make_scorer(recall_score)},
                    refit='accuracy')
grid.fit(X_train, y_train)

print(classification_report(y_test, grid.predict(X_test)))

              precision    recall  f1-score   support

           0       0.66      0.93      0.77       107
           1       0.74      0.28      0.40        72

    accuracy                           0.67       179
   macro avg       0.70      0.61      0.59       179
weighted avg       0.69      0.67      0.62       179


In [10]:
# Podem veure quin ha estat el millor preu mínim
grid.best_params_

{'preu_minim': 48.275862068965516}

### Exploració interactiva

Ara que ja hem vist que el preu del bitllet no és una bona variable per predir si un passatger va sobreviure o no, podem explorar les dades per trobar una variable millor.

Per fer-ho, utilitzarem la funció InteractiveCharts. Aquesta funció ens permetrà explorar les dades de forma interactiva. En aquest cas, utilitzarem la funció parallel_coordinates per veure com es distribueixen les dades en funció de les variables explicatives.

In [11]:
from hulearn.experimental.interactive import parallel_coordinates

parallel_coordinates(df, label="survived", height=200)

Partint de la hipótesi que les dones i els nens van tenir més probabilitats de sobreviure, podem explorar les dades per veure si es veritat i sembla que  sí (comptant amb les diferències de classe social): Si Solament deixem les dones i els nens de 1a i 2a classe, la majoria van sobreviure.

Així doncs, podem crear un classificador que utilitzi el sexe, la edat i la classe del passatger per predir si va sobreviure o no.

In [12]:
def classificador_edat_sexe_classe(df, edat=12):
    """
    Classifica els passatgers en funció del sexe, la edat i la classe del passatger
    El plantejament és que les dones i els nens van tenir més probabilitats de sobreviure
    """
    regla_dones = (df['pclass'] < 3.0) & (df['sex'] == "female")
    regla_nens = (df['pclass'] < 3.0) & (df['age'] <= edat)
    return regla_dones | regla_nens


mod = FunctionClassifier(classificador_edat_sexe_classe)
mod.fit(X_train, y_train)
mod.score(X_test, y_test)

0.8212290502793296

In [13]:
grid = GridSearchCV(mod,
                    cv=2,
                    param_grid={'edat': np.linspace(0, 50, 50)},
                    scoring={'accuracy': make_scorer(accuracy_score),
                             'precision': make_scorer(precision_score),
                             'recall': make_scorer(recall_score)},
                    refit='accuracy')
grid.fit(X_train, y_train)

print(grid.best_params_)
predict = grid.predict(X_train)

print(predict)
print(classification_report(y_test, grid.predict(X_test)))

{'edat': 3.0612244897959187}
649    False
360    False
518    False
248     True
344    False
       ...  
71     False
106    False
270     True
435    False
102    False
Length: 535, dtype: bool
              precision    recall  f1-score   support

           0       0.76      0.97      0.86       107
           1       0.93      0.56      0.70        72

    accuracy                           0.80       179
   macro avg       0.85      0.76      0.78       179
weighted avg       0.83      0.80      0.79       179


Els nombres son prou millors que els anteriors. Així doncs, podem utilitzar aquest classificador per fer prediccions sobre nous passatgers.

## FIGS

FIGS és una llibreria que ens permet crear regles per classificar les dades. En aquest cas, utilitzarem les dades del Titanic per crear regles que ens permetin predir si un passatger va sobreviure o no.

In [14]:
# instal·lem la llibreria
!pip install imodels


[notice] A new release of pip available: 22.3.1 -> 23.3.2
[notice] To update, run: pip install --upgrade pip


In [15]:
# Carreguem la llibreria
from imodels import FIGSClassifier

In [16]:
# Preparem les dades
X_skope = df.drop(columns=['name', 'sibsp'])
X_skope['sex'] = X_skope['sex'].replace(['female', 'male'], [0, 1])

X_train, X_test, y_train, y_test = train_test_split(
    X_skope.drop(['survived'], axis=1), X_skope['survived'], test_size=0.25, random_state=42)

In [17]:
# Creem el classificador
clf = FIGSClassifier(max_rules=4)
# Entrenem el classificador
clf.fit(X_train, y_train)

FIGSClassifier(max_rules=4)

In [18]:
# Podem veure el rendiment del classificador
print(classification_report(y_test, clf.predict(X_test)))

              precision    recall  f1-score   support

           0       0.76      0.96      0.85       107
           1       0.91      0.54      0.68        72

    accuracy                           0.79       179
   macro avg       0.83      0.75      0.76       179
weighted avg       0.82      0.79      0.78       179


Podem observar que les regles que ha creat el classificador tenen un rendiment semblant al classificador que hem creat amb Human learn i els conceptes que hem creat amb Human learn són més fàcils d'interpretar i podem seguir afegint regles per millorar el rendiment del classificador (per exemple, podríem incorporar la variable `fare`).